In [3]:
import pandas as pd
import os
import warnings
import numpy as np
from sklearn.preprocessing import StandardScaler

In [5]:
app_dir = os.path.dirname(os.path.abspath(r"C:\Users\Divit\Desktop\MovieRecommender\Code\recommenderapp\app.py"))
code_dir = os.path.dirname(app_dir)
project_dir = os.path.dirname(code_dir)

warnings.filterwarnings("ignore")

In [9]:
def recommendForNewUser(user_rating):
    # Load data
    ratings = pd.read_csv(project_dir + "/data/ratings.csv")
    movies = pd.read_csv(project_dir + "/data/movies.csv")
    
    # Merge user ratings with movie data
    user_ratings_df = pd.DataFrame(user_rating, columns=["title", "rating"])
    user_movie_ratings = pd.merge(user_ratings_df, movies, on="title", how="inner")
    
    # Normalize user ratings
    user_movie_ratings["rating"] = StandardScaler().fit_transform(user_movie_ratings[["rating"]])
    
    # Calculate user profile
    user_profile = user_movie_ratings.groupby("genres").mean()["rating"].reset_index()
    
    # Calculate movie genre similarity with user profile
    movies["recommended"] = movies["genres"].apply(
        lambda x: sum(user_profile[user_profile["genres"].isin(x)]["rating"])
    )
    
    # Sort movies by recommendation score
    recommended_movies = movies.sort_values(by="recommended", ascending=False)
    
    # Exclude movies the user has already rated
    recommended_movies = recommended_movies[~recommended_movies["title"].isin(user_ratings_df["title"])]
    
    print(recommended_movies.head(20)["title"].tolist())


In [7]:
recommended_movies

NameError: name 'recommended_movies' is not defined

In [12]:
movies = pd.read_csv(project_dir + "/data/movies.csv")


In [13]:
movies

movieId                                      title  \
0           1                           Toy Story (1995)   
1           2                             Jumanji (1995)   
2           3                    Grumpier Old Men (1995)   
3           4                   Waiting to Exhale (1995)   
4           5         Father of the Bride Part II (1995)   
...       ...                                        ...   
9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   193583               No Game No Life: Zero (2017)   
9739   193585                               Flint (2017)   
9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  
0     Adventure|Animation|Children|Comedy|Fantasy  
1                      Adventure|Children|Fantasy  
2                                  Comedy|Romance  
3                            Comedy|Drama|Romance  
4                                          Comedy  
...                                           ...  
9737              Action|Animation|Comedy|Fantasy  
9738                     Animation|Comedy|Fantasy  
9739                                        Drama  
9740                             Action|Animation  
9741                                       Comedy  

[9742 rows x 3 columns]

In [14]:
ratings = pd.read_csv(project_dir + "/data/ratings.csv")
ratings

userId  movieId  rating   timestamp
0            1        1     4.0   964982703
1            1        3     4.0   964981247
2            1        6     4.0   964982224
3            1       47     5.0   964983815
4            1       50     5.0   964982931
...        ...      ...     ...         ...
100831     610   166534     4.0  1493848402
100832     610   168248     5.0  1493850091
100833     610   168250     5.0  1494273047
100834     610   168252     5.0  1493846352
100835     610   170875     3.0  1493846415

[100836 rows x 4 columns]

In [37]:
def recommendForNewUser(user_rating):    
    ratings = pd.read_csv(os.path.join(project_dir, "data/ratings.csv"))
    movies = pd.read_csv(os.path.join(project_dir, "data/movies.csv"))
    user = pd.DataFrame(user_rating)

    # Merge user's ratings with movie data to get movie IDs
    userMovieID = movies[movies["title"].isin(user["title"])]
    userRatings = pd.merge(userMovieID, user)
    print(userRatings)

    # Create a dictionary of movie genres
    movie_genres = movies["genres"].str.split("|").apply(lambda x: x.tolist()).tolist()
    genres = pd.DataFrame(movie_genres, columns=["genres"])

    # Create a dictionary of user preferences
    user_preferences = userRatings["rating"].tolist()

    # Function to calculate similarity between user ratings and movie genres
    def userRatingSimilarity(genres, user_preferences, df):
        user_ratings = df.pivot_table(index="movieId", values="rating")
        user_ratings = user_ratings.fillna(0)
        similarity = user_ratings.dot(user_preferences) / (user_ratings.apply(lambda x: x.pow(2)).sum().pow(0.5) * sum(user_preferences))
        return similarity

    # Use cosine similarity to find similar users
    similar_users = pd.DataFrame(index=userRatings.userId)
    for user_id in userRatings.userId:
        similar_users.loc[user_id] = userRatingSimilarity(genres, user_preferences, ratings[ratings.userId == user_id])

    # Find similar movies
    similar_movies = pd.DataFrame(index=genres.genres)
    for genre_id in genres.genres:
        similar_movies.loc[genre_id] = userRatingSimilarity(genres, user_preferences, ratings[ratings.genres.str.contains(genre_id)])

    # Find recommended movies for the new user
    recommendations = similar_users.dot(ratings.movieId.apply(lambda x: similar_movies.loc[x] if x in similar_movies.index else pd.Series(0, index=similar_movies.index)))

    # Sort and return the top recommended movies
    recommendations = recommendations.sort_values(ascending=False)
    recommended_movie_ids = recommendations.index
    recommended_movies = movies[movies["movieId"].isin(recommended_movie_ids)]
    return recommended_movies[["movieId", "title", "genres"]]



In [50]:
    ratings = pd.read_csv(project_dir + "/data/ratings.csv")
    movies = pd.read_csv(project_dir + "/data/movies.csv")
    user = pd.DataFrame(user_rating)

    # Merge user's ratings with movie data to get movie IDs
    userRatings = pd.merge(ratings, movies, on="movieId")
    
    # Create a dictionary of movie genres
    movie_genres = movies["genres"].str.split("|")
    genres = pd.DataFrame(movie_genres, columns=["genres"])
    
    user_preferences = userRatings.pivot(index="movieId", columns="userId", values="rating")
    user_preferences = user_preferences.fillna(0)
    
    user_profile = userRatingSimilarity(user_preferences, genres)

    # Calculate movie scores based on user's profile
    movie_scores = genres.dot(user_profile.T)

    # Sort and return the top recommended movies
    recommended_movies = movies.copy()
    recommended_movies["score"] = movie_scores.values[0]
    recommended_movies = recommended_movies.sort_values(by="score", ascending=False)
    
    return recommended_movies[["movieId", "title", "genres"]]


ValueError: matrices are not aligned

In [58]:
def userRatingSimilarity(user_profile, genres):
    movie_scores = user_profile.dot(genres.T)
    return movie_scores


In [93]:
    ratings = pd.read_csv(project_dir + "/data/ratings.csv")
    movies = pd.read_csv(project_dir + "/data/movies.csv")
    user = pd.DataFrame(user_rating)

    # Merge user's ratings with movie data to get movie IDs
    userRatings = pd.merge(ratings, movies, on="movieId")

    # Create a dictionary of movie genres
    movie_genres = movies["genres"].str.split("|")
    genres = pd.DataFrame(movie_genres, columns=["genres"])

    # Create a dictionary of user preferences
    user_preferences = userRatings.pivot_table(index="userId", columns="movieId", values="rating", fill_value=0)

    user_genre_preferences = np.align(user_preferences, genres, 'first')
    # Perform the dot product
    movie_scores = user_genre_preferences.dot(genres.T)
        # Sort and return the top recommended movies
    recommended_movies = movies.copy()
    recommended_movies["score"] = movie_scores.values[0]
    recommended_movies = recommended_movies.sort_values(by="score", ascending=False)
    
    return recommended_movies[["movieId", "title", "genres"]]



AttributeError: module 'numpy' has no attribute 'align'

In [77]:
    import pandas as pd
    import os

# Set the project directory
    project_dir = os.path.dirname(os.path.abspath(r"C:\Users\Divit\Desktop\MovieRecommender\Code"))


    ratings = pd.read_csv(project_dir + "/data/ratings.csv")
    movies = pd.read_csv(project_dir + "/data/movies.csv")
    user = pd.DataFrame(user_rating)
    userMovieID = movies[movies["title"].isin(user["title"])]
    userRatings = pd.merge(userMovieID, user)

    moviesGenreFilled = movies.copy(deep=True)
    copyOfMovies = movies.copy(deep=True)
    for index, row in copyOfMovies.iterrows():
        copyOfMovies.at[index, "genres"] = row["genres"].split("|")
    for index, row in copyOfMovies.iterrows():
        for genre in row["genres"]:
            moviesGenreFilled.at[index, genre] = 1
    moviesGenreFilled = moviesGenreFilled.fillna(0)

    userGenre = moviesGenreFilled[moviesGenreFilled.movieId.isin(userRatings.movieId)]
    userGenre.drop(["movieId", "title", "genres"], axis=1, inplace=True)
    userProfile = userGenre.T.dot(userRatings.rating.to_numpy())
    moviesGenreFilled.set_index(moviesGenreFilled.movieId)
    moviesGenreFilled.drop(["movieId", "title", "genres"], axis=1, inplace=True)

    recommendations = (moviesGenreFilled.dot(userProfile)) / userProfile.sum()
    joinMoviesAndRecommendations = movies.copy(deep=True)
    joinMoviesAndRecommendations["recommended"] = recommendations
    joinMoviesAndRecommendations.sort_values(
        by="recommended", ascending=False, inplace=True
    )
    print([x for x in joinMoviesAndRecommendations["title"]][:201])




["Twelve Tasks of Asterix, The (Les douze travaux d'Astérix) (1976)", 'Who Framed Roger Rabbit? (1988)', 'TMNT (Teenage Mutant Ninja Turtles) (2007)', 'The Lego Movie (2014)', 'Adventures of Rocky and Bullwinkle, The (2000)', 'Turbo (2013)', 'Antz (1998)', 'Puss in Boots (Nagagutsu o haita neko) (1969)', 'Asterix and the Vikings (Astérix et les Vikings) (2006)', 'Space Jam (1996)', 'Gnomeo & Juliet (2011)', 'Shrek Forever After (a.k.a. Shrek: The Final Chapter) (2010)', 'Toy Story 3 (2010)', 'Tale of Despereaux, The (2008)', 'Toy Story (1995)', "Emperor's New Groove, The (2000)", 'Enchanted (2007)', 'Shrek the Third (2007)', 'Shrek (2001)', 'Ant Bully, The (2006)', 'Moana (2016)', 'Wild, The (2006)', 'Monsters, Inc. (2001)', 'Valiant (2005)', 'Robots (2005)', 'The Good Dinosaur (2015)', 'Toy Story 2 (1999)', 'Home (2015)', 'Inside Out (2015)', 'Pagemaster, The (1994)', 'G.I. Joe: The Movie (1987)', 'Super Mario Bros. (1993)', 'Goonies, The (1985)', 'Laputa: Castle in the Sky (Tenkû no 

In [119]:
import pandas as pd
import os
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel

app_dir = os.path.dirname(os.path.abspath(r"C:\Users\Divit\Desktop\MovieRecommender\Code\recommenderapp\app.py"))
code_dir = os.path.dirname(app_dir)
project_dir = os.path.dirname(code_dir)

def recommend_for_new_user(user_rating, num_recommendations=10):
    # Load data
    ratings = pd.read_csv(os.path.join(project_dir, "data", "ratings.csv"))
    movies = pd.read_csv(os.path.join(project_dir, "data", "movies.csv"))

    # Merge user ratings with movie data using movieId
    user_ratings = pd.DataFrame(user_rating, columns=["movieId", "rating"])
    user_movie_ratings = pd.merge(movies, user_ratings, on="movieId", how="inner")

    # Create a TF-IDF vectorizer for movie genres
    tfidf_vectorizer = TfidfVectorizer(stop_words='english')
    movies['genres'] = movies['genres'].fillna('')
    tfidf_matrix = tfidf_vectorizer.fit_transform(movies['genres'])

    # Calculate cosine similarities between movies
    cosine_similarities = linear_kernel(tfidf_matrix, tfidf_matrix)

    # Create a mapping of movie titles to their indices
    movie_indices = pd.Series(movies.index, index=movies['movieId'])

    # Find the index of each movie in the user's ratings
    user_movie_indices = user_movie_ratings['movieId'].map(movie_indices)

    # Initialize a dictionary to store recommendations for each user rating
    recommended_movies = {}

    # Compute recommendations for each user rating
    for idx in user_movie_indices:
        similar_scores = list(enumerate(cosine_similarities[idx]))
        similar_scores = sorted(similar_scores, key=lambda x: x[1], reverse=True)
        similar_scores = similar_scores[1:num_recommendations+1]  # Exclude the current movie
        movie_indices = [x[0] for x in similar_scores]
        top_movies = movies.iloc[movie_indices]
        recommended_movies[user_movie_ratings.loc[user_movie_ratings['movieId'] == user_movie_indices.iloc[0], 'movieId'].values[0]] = list(top_movies['title'][:num_recommendations])

    return recommended_movies

# Example usage:
user_rating = [(1, 5), (2, 4)]  # Use movieIds instead of titles
recommended_movies = recommend_for_new_user(user_rating, num_recommendations=10)

for movie_id, recommendations in recommended_movies.items():
    print(f"For movie ID {movie_id}, recommended movies are:")
    for rec_movie in recommendations:
        print(rec_movie)


IndexError: index 0 is out of bounds for axis 0 with size 0

In [128]:
# for i in range(len(df["genres"])):
df=pd.read_csv(os.path.join(project_dir, "data", "movies.csv"))
for i in range(len(df)):
    a = df["genres"][i].split("|")
    # print(a)
    for j in a:
        # if j exists in df
        # print(j)
        if j in df:
            df[j][i] = 1
        else:
            df[j] = 0*len(df["genres"])
            df[j][i] = 1
df



movieId                                      title  \
0           1                           Toy Story (1995)   
1           2                             Jumanji (1995)   
2           3                    Grumpier Old Men (1995)   
3           4                   Waiting to Exhale (1995)   
4           5         Father of the Bride Part II (1995)   
...       ...                                        ...   
9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   193583               No Game No Life: Zero (2017)   
9739   193585                               Flint (2017)   
9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  Adventure  Animation  \
0     Adventure|Animation|Children|Comedy|Fantasy          1          1   
1                      Adventure|Children|Fantasy          1          0   
2                                  Comedy|Romance          0          0   
3                            Comedy|Drama|Romance          0          0   
4                                          Comedy          0          0   
...                                           ...        ...        ...   
9737              Action|Animation|Comedy|Fantasy          0          1   
9738                     Animation|Comedy|Fantasy          0          1   
9739                                        Drama          0          0   
9740                             Action|Animation          0          1   
9741                                       Comedy          0          0   

      Children  Comedy  Fantasy  Romance  Drama  ...  Horror  Mystery  Sci-Fi  \
0            1       1        1        0      0  ...       0        0       0   
1            1       0        1        0      0  ...       0        0       0   
2            0       1        0        1      0  ...       0        0       0   
3            0       1        0        1      1  ...       0        0       0   
4            0       1        0        0      0  ...       0        0       0   
...        ...     ...      ...      ...    ...  ...     ...      ...     ...   
9737         0       1        1        0      0  ...       0        0       0   
9738         0       1        1        0      0  ...       0        0       0   
9739         0       0        0        0      1  ...       0        0       0   
9740         0       0        0        0      0  ...       0        0       0   
9741         0       1        0        0      0  ...       0        0       0   

      War  Musical  Documentary  IMAX  Western  Film-Noir  (no genres listed)  
0       0        0            0     0        0          0                   0  
1       0        0            0     0        0          0                   0  
2       0        0            0     0        0          0                   0  
3       0        0            0     0        0          0                   0  
4       0        0            0     0        0          0                   0  
...   ...      ...          ...   ...      ...        ...                 ...  
9737    0        0            0     0        0          0                   0  
9738    0        0            0     0        0          0                   0  
9739    0        0            0     0        0          0                   0  
9740    0        0            0     0        0          0                   0  
9741    0        0            0     0        0          0                   0  

[9742 rows x 23 columns]

In [8]:
from sklearn.metrics.pairwise import cosine_similarity
# Load the movies data
df = pd.read_csv(os.path.join(project_dir, "data", "movies.csv"))

# Split genres and create binary indicator columns
genre_columns = df["genres"].str.get_dummies("|")

# Concatenate the genre columns with the original DataFrame
df = pd.concat([df, genre_columns], axis=1)

# Drop the original "genres" column
df.drop("genres", axis=1, inplace=True)

# Calculate cosine similarity between movies based on genre columns
cosine_sim = cosine_similarity(genre_columns, genre_columns)

# Create a DataFrame to store the similarity scores
similarity_df = pd.DataFrame(cosine_sim, index=df["movieId"], columns=df["movieId"])

# Create a dictionary to store the top 10 similar movies for each movie
top_similar_movies = {}

# Find the top 10 similar movies for each movie
for movie_id, row in similarity_df.iterrows():
    similar_movies = row.sort_values(ascending=False)[1:11].index.tolist()  # Exclude the movie itself
    top_similar_movies[movie_id] = similar_movies

# Print the top 10 similar movies for each movie
for movie_id, similar_movies in top_similar_movies.items():
    movie_title = df[df["movieId"] == movie_id]["title"].values[0]
    print(f"Top 10 movies similar to '{movie_title}':")
    for sim_movie_id in similar_movies:
        sim_movie_title = df[df["movieId"] == sim_movie_id]["title"].values[0]
        print(f"   {sim_movie_title}")


Top 10 movies similar to 'Toy Story (1995)':
   Turbo (2013)
   Monsters, Inc. (2001)
   Moana (2016)
   Emperor's New Groove, The (2000)
   Adventures of Rocky and Bullwinkle, The (2000)
   Toy Story 2 (1999)
   Wild, The (2006)
   The Good Dinosaur (2015)
   Tale of Despereaux, The (2008)
   Asterix and the Vikings (Astérix et les Vikings) (2006)
Top 10 movies similar to 'Jumanji (1995)':
   Chronicles of Narnia: Prince Caspian, The (2008)
   Golden Compass, The (2007)
   NeverEnding Story, The (1984)
   Water Horse: Legend of the Deep, The (2007)
   Chronicles of Narnia: The Voyage of the Dawn Treader, The (2010)
   Escape to Witch Mountain (1975)
   Alice in Wonderland (1933)
   Percy Jackson: Sea of Monsters (2013)
   Indian in the Cupboard, The (1995)
   Santa Claus: The Movie (1985)
Top 10 movies similar to 'Grumpier Old Men (1995)':
   When in Rome (2010)
   Say It Isn't So (2001)
   Leap Year (2010)
   The Girls (1961)
   Bart Got a Room (2008)
   Sure Thing, The (1985)
   Val

   Soul Food (1997)
   Sweet Sixteen (2002)
   Solas (1999)
   Elephant (2003)
   Radio (2003)
   Star Maps (1997)
Top 10 movies similar to 'Twelve Monkeys (a.k.a. 12 Monkeys) (1995)':
   District 9 (2009)
   Twelve Monkeys (a.k.a. 12 Monkeys) (1995)
   Unforgettable (1996)
   Narcopolis (2014)
   Seconds (1966)
   Soylent Green (1973)
   Invasion of the Body Snatchers (1978)
   Coherence (2013)
   Predestination (2014)
   Cube Zero (2004)
Top 10 movies similar to 'Babe (1995)':
   Yearling, The (1946)
   Babe (1995)
   Shiloh (1997)
   Little Princess, The (1939)
   Railway Children, The (1970)
   National Velvet (1944)
   Risen (2016)
   Now and Then (1995)
   Heidi (1937)
   My Dog Skip (1999)
Top 10 movies similar to 'Dead Man Walking (1995)':
   No Man's Land (1987)
   Pickpocket (1959)
   No Country for Old Men (2007)
   Young and the Damned, The (Olvidados, Los) (1950)
   Man Who Wasn't There, The (2001)
   Drugstore Cowboy (1989)
   Heist (2001)
   Bonnie and Clyde (1967)
   Sh

   Snakes on a Plane (2006)
   Machine Girl, The (Kataude mashin gâru) (2008)
   Haunted World of El Superbeasto, The (2009)
   Pusher III: I'm the Angel of Death (2005)
   Behind the Mask: The Rise of Leslie Vernon (2006)
   Housebound (2014)
   Massu Engira Maasilamani (2015)
   Horde, The (La Horde) (2009)
   Severance (2006)
Top 10 movies similar to 'Fair Game (1995)':
   Vigilante Diaries (2016)
   Invincible Shaolin (1978)
   Fair Game (1995)
   Jason Bourne (2016)
   Five Deadly Venoms (1978)
   Master of the Flying Guillotine (Du bi quan wang da po xue di zi) (1975)
   Marauders (2016)
   Best of the Best 3: No Turning Back (1995)
   Knock Off (1998)
   Punisher, The (1989)
Top 10 movies similar to 'Kicking and Screaming (1995)':
   Cook the Thief His Wife & Her Lover, The (1989)
   California Split (1974)
   Charlie Bartlett (2007)
   Carnal Knowledge (1971)
   Ruling Class, The (1972)
   Your Friends and Neighbors (1998)
   The African Doctor (2016)
   Good bye, Lenin! (2003)

   101 Dalmatians (1996)
   Muppets Take Manhattan, The (1984)
   To Grandmother's House We Go (1992)
Top 10 movies similar to 'Catwalk (1996)':
   Baraka (1992)
   Stevie (2002)
   DiG! (2004)
   Riding Giants (2004)
   Happy People: A Year in the Taiga (2010)
   Outfoxed: Rupert Murdoch's War on Journalism (2004)
   Indie Game: The Movie (2012)
   Marwencol (2010)
   Grey Gardens (1975)
   Promises (2001)
Top 10 movies similar to 'Braveheart (1995)':
   Monuments Men, The (2014)
   Behind Enemy Lines (2001)
   Gods and Generals (2003)
   Boot, Das (Boat, The) (1981)
   Fighting Seabees, The (1944)
   Longest Day, The (1962)
   To End All Wars (2001)
   Ip Man (2008)
   Apocalypse Now (1979)
   All Quiet on the Western Front (1930)
Top 10 movies similar to 'Taxi Driver (1976)':
   Sea of Love (1989)
   Yellow Sea, The (a.k.a. The Murderer) (Hwanghae) (2010)
   Traffic (2000)
   Samouraï, Le (Godson, The) (1967)
   Marathon Man (1976)
   Bring Me the Head of Alfredo Garcia (1974)
   In

   Spartacus (1960)
   Flying Tigers (1942)
   Sands of Iwo Jima (1949)
   Rob Roy (1995)
   Pearl Harbor (2001)
   Robin Hood (2010)
   El Cid (1961)
   Cold Mountain (2003)
   House of Flying Daggers (Shi mian mai fu) (2004)
Top 10 movies similar to 'Addiction, The (1995)':
   Begotten (1990)
   Angst  (1983)
   Interview with the Vampire: The Vampire Chronicles (1994)
   Confessions (Kokuhaku) (2010)
   Dr. Jekyll and Mr. Hyde (1931)
   Wendigo (2001)
   Thirst (Bakjwi) (2009)
   May (2002)
   Dr. Jekyll and Mr. Hyde (1941)
   Gothic (1986)
Top 10 movies similar to 'Batman Forever (1995)':
   Crime Busters (1977)
   Nothing to Lose (1997)
   Batman Forever (1995)
   Rumble in the Bronx (Hont faan kui) (1995)
   It's a Mad, Mad, Mad, Mad World (1963)
   Kingsman: The Secret Service (2015)
   After the Sunset (2004)
   Charlie's Angels: Full Throttle (2003)
   Diamond Arm, The (Brilliantovaya ruka) (1968)
   Hancock (2008)
Top 10 movies similar to 'Beauty of the Day (Belle de jour) (1

...

   Riding Giants (2004)
   Happy People: A Year in the Taiga (2010)
   Outfoxed: Rupert Murdoch's War on Journalism (2004)
   Indie Game: The Movie (2012)
   Marwencol (2010)
   Grey Gardens (1975)
   Promises (2001)
Top 10 movies similar to 'Self-criticism of a Bourgeois Dog (2017)':
   Walk of Shame (2014)
   Ferris Bueller's Day Off (1986)
   Fading Gigolo (2013)
   Risky Business (1983)
   Superstar (1999)
   Happy, Texas (1999)
   Neighbors (2014)
   Be Kind Rewind (2008)
   Mom's Night Out (2014)
   Chef (2014)
Top 10 movies similar to 'Der Herr Karl (1961)':
   Walk of Shame (2014)
   Ferris Bueller's Day Off (1986)
   Fading Gigolo (2013)
   Risky Business (1983)
   Superstar (1999)
   Happy, Texas (1999)
   Neighbors (2014)
   Be Kind Rewind (2008)
   Mom's Night Out (2014)
   Chef (2014)
Top 10 movies similar to 'LEGO DC Super Hero Girls: Brain Drain (2017)':
   A Plasticine Crow (1981)
   Invincible Iron Man, The (2007)
   Asterix: The Land of the Gods (Astérix: Le domaine d

   Outfoxed: Rupert Murdoch's War on Journalism (2004)
   Indie Game: The Movie (2012)
   Marwencol (2010)
   Grey Gardens (1975)
   Promises (2001)
Top 10 movies similar to 'Christina P: Mother Inferior (2017)':
   Walk of Shame (2014)
   Ferris Bueller's Day Off (1986)
   Fading Gigolo (2013)
   Risky Business (1983)
   Superstar (1999)
   Happy, Texas (1999)
   Neighbors (2014)
   Be Kind Rewind (2008)
   Mom's Night Out (2014)
   Chef (2014)
Top 10 movies similar to 'Jumanji: Welcome to the Jungle (2017)':
   Turbo: A Power Rangers Movie (1997)
   Jumanji: Welcome to the Jungle (2017)
   Sky High (2005)
   Dragon Ball: Mystical Adventure (Doragon bôru: Makafushigi dai bôken) (1988)
   Agent Cody Banks (2003)
   Incredibles 2 (2018)
   Dragon Ball: Sleeping Princess in Devil's Castle (Doragon bôru: Majinjô no nemuri hime) (1987)
   Solo: A Star Wars Story (2018)
   Inspector Gadget (1999)
   G-Force (2009)
Top 10 movies similar to 'Dane Cook: Troublemaker (2014)':
   Walk of Shame (

   Hotel Transylvania (2012)
   Shark Tale (2004)
   Wallace & Gromit: A Close Shave (1995)
   Winnie the Pooh (2011)
   Rugrats in Paris: The Movie (2000)
Top 10 movies similar to 'The Second Renaissance Part II (2003)':
   A Detective Story (2003)
   Time Masters (Maîtres du temps, Les) (1982)
   Ghost in the Shell (Kôkaku kidôtai) (1995)
   The Second Renaissance Part II (2003)
   Fantastic Planet, The (Planète sauvage, La) (1973)
   Kid's Story (2003)
   Metropolis (2001)
   Patlabor 2: The Movie (1993)
   The Electric Hotel (1908)
   Ultimate Avengers 2 (2006)
Top 10 movies similar to 'Annihilation (2018)':
   Seconds (1966)
   Saturn 3 (1980)
   Black Sea (2015)
   Narcopolis (2014)
   Twelve Monkeys (a.k.a. 12 Monkeys) (1995)
   Unforgettable (1996)
   Supernova (2000)
   Stepford Wives, The (1975)
   The Hunger Games: Mockingjay - Part 1 (2014)
   The 5th Wave (2016)
Top 10 movies similar to 'A Christmas Story Live! (2017)':
   Pirates of the Caribbean: Dead Men Tell No Tales (

   Charlie Bartlett (2007)
   Carnal Knowledge (1971)
   Ruling Class, The (1972)
   Your Friends and Neighbors (1998)
   The African Doctor (2016)
   Good bye, Lenin! (2003)
   Simpatico (1999)
   Mental (2012)
Top 10 movies similar to 'A Quiet Place (2018)':
   Innocents, The (1961)
   My Bloody Valentine (1981)
   Body Snatcher, The (1945)
   Body (2015)
   Peeping Tom (1960)
   Split (2017)
   Hannibal Rising (2007)
   Dark Water (2005)
   Messengers, The (2007)
   Misery (1990)
Top 10 movies similar to 'Alpha (2018)':
   Joy Ride (2001)
   Nancy Drew (2007)
   From Russia with Love (1963)
   Goldfinger (1964)
   Broken Arrow (1996)
   127 Hours (2010)
   Anaconda (1997)
   Lord of the Flies (1963)
   Maximum Risk (1996)
   Missing, The (2003)
Top 10 movies similar to 'I Kill Giants (2018)':
   Tideland (2005)
   Pan's Labyrinth (Laberinto del fauno, El) (2006)
   Seventh Sign, The (1988)
   Byzantium (2012)
   Twilight (2008)
   Goodnight Mommy (Ich seh ich seh) (2014)
   Fallen (

   Justice League: Crisis on Two Earths (2010)
Top 10 movies similar to 'anohana: The Flower We Saw That Day - The Movie (2013)':
   Persepolis (2007)
   Man Who Planted Trees, The (Homme qui plantait des arbres, L') (1987)
   Animal Farm (1954)
   anohana: The Flower We Saw That Day - The Movie (2013)
   Wrinkles (Arrugas) (2011)
   Only Yesterday (Omohide poro poro) (1991)
   Tale of Princess Kaguya, The (Kaguyahime no monogatari) (2013)
   Angel's Egg (Tenshi no tamago) (1985)
   Mary and Max (2009)
   Loving Vincent (2017)
Top 10 movies similar to 'Silver Spoon (2014)':
   Cook the Thief His Wife & Her Lover, The (1989)
   California Split (1974)
   Charlie Bartlett (2007)
   Carnal Knowledge (1971)
   Ruling Class, The (1972)
   Your Friends and Neighbors (1998)
   The African Doctor (2016)
   Good bye, Lenin! (2003)
   Simpatico (1999)
   Mental (2012)
Top 10 movies similar to 'Love Live! The School Idol Movie (2015)':
   A Plasticine Crow (1981)
   Invincible Iron Man, The (2007

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

movies_df = pd.read_csv(os.path.join(project_dir, "data", "movies.csv"))

# Split genres and create binary indicator columns
genre_columns = movies_df["genres"].str.get_dummies("|")

# Concatenate the genre columns with the original DataFrame
movies_df = pd.concat([movies_df, genre_columns], axis=1)

# Drop the original "genres" column
movies_df.drop("genres", axis=1, inplace=True)

# Load the ratings data
ratings_df = pd.read_csv(os.path.join(project_dir, "data", "ratings.csv"))

# Merge the dataframes on "movieId" using an inner join
merged_df = pd.merge(movies_df, ratings_df, on="movieId", how="inner")

# Calculate cosine similarity between movies based on genre columns
cosine_sim = cosine_similarity(genre_columns, genre_columns)

# Create a DataFrame to store the similarity scores
similarity_df = pd.DataFrame(cosine_sim, index=movies_df["movieId"], columns=movies_df["movieId"])

# Print the top 10 similar movies for each movie
for movie_id, similar_movies in top_similar_movies.items():
    movie_title = movies_df[movies_df["movieId"] == movie_id]["title"].values[0]
    print(f"Top 10 movies similar to '{movie_title}':")
    for sim_movie_id in similar_movies:
        sim_movie_title = movies_df[movies_df["movieId"] == sim_movie_id]["title"].values[0]
        # Calculate the match percentage based on genre similarity
        match_percentage = similarity_df.loc[movie_id, sim_movie_id] * 100
        print(f"   {sim_movie_title} - Match Percentage: {match_percentage:.2f}%")

# Sort the merged DataFrame by movie ratings in descending order
sorted_df = merged_df.sort_values(by="rating", ascending=False)
if movieId==1388:
# Print the sorted DataFrame by movie ratings
    print(sorted_df[["movieId", "title", "rating"]])
